#  MentalQA Dataset Description

The full dataset consists of **500 annotated samples**. For the purpose of this shared task, we are using only the **training and development set**:

- **Train+Dev Set**: 350 samples  
- **Test Set**: 150 samples (withheld for evaluation purposes)

---

###  Dataset File: `MentalQA_500_data.csv` (tab-separated)

This dataset was recently accepted in the *IEEE ACCESS* journal.  
It contains **four columns** as follows:

1. **Question**  
2. **Answer**  
3. **Question Types** (`final_QT`)  
4. **Answer Strategies** (`final_AS`)

---

###  Question Type Labels (`final_QT`)

| Label | Name                       |Description |
|----------|----------------------------|----------------
| A        | **Diagnosis**              | Questions about clinical findings, tests, disease criteria, and manifestations. |
| B        | **Treatment**              | Questions about therapies, drug use, side effects, and contraindications. |
| C        | **Anatomy and Physiology** | Basic medical knowledge (e.g., tissues, organs, metabolism). |
| D        | **Epidemiology**           | Disease progression, prognosis, etiology, and risk factors. |
| E        | **Healthy Lifestyle**      | Diet, exercise, mood, and lifestyle factors affecting mental health. |
| F        | **Provider Choices**       | Recommendations for doctors, hospitals, or medical departments. |
| Z        | **Other**                  | General or uncategorized questions. |

---

###  Answer Strategy Labels (`final_AS`)

| Label   | Name              | Description |
|---------|-----------|-------------|
| 1       | **Information**    | Provides factual data, explanations, or resources. |
| 2       |  **Direct Guidance**| Offers suggestions, instructions, or behavioral advice. |
| 3       | **Emotional Support** | Gives reassurance, empathy, or emotional encouragement. |





GitHub: https://github.com/hasanhuz/MentalQA/tree/main

Paper: https://arxiv.org/abs/2405.12619

In [ ]:
!pip install openai==0.28
!pip install bert-score
!pip install -U langchain langchain-community
!pip install -U langchain-groq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.5/76.5 kB 7.1 MB/s eta 0:00:00
  Attempting uninstall: openai
    Found existing installation: openai 1.98.0
    Uninstalling openai-1.98.0:
      Successfully uninstalled openai-1.98.0
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 5.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 94.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 76.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 52.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 1.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 12.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/2

In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from collections import Counter

In [ ]:
pd.set_option("display.max_colwidth", None, "display.max_rows", None)

In [ ]:
data = pd.read_csv('/content/Train_Dev.tsv', sep='\t')
data.sample(3)

question  \
146                                                                                                  انا شاب اعاني من الرهاب الاجتماعي منذ الطفولة وصعوبة في تكوين الصداقات والمعارف وزاد مرضى في الآونة الأخيرة بصورة كبيرة حيث تعطلت حياتي أكثر واصبحت حياتي أكثر تعقيدا من السابق ارجو المساعدة وشكرا   
222  السلام عليكم .فتاة ابلغ ال 17 عشر و اشعر انني لست بخير و هذا منذ القدم لكنني لم الحظ هذا الا قبل اسبوع او اكثر اعاني من تقلب مزاجي السريع جدا مثلا ان كنت حزينة فأصبح سعيدة في غضون دقائق ثم اغضب و ابتسم في وسط غضبي ...ابكي بعدها لا مكالمة طبيعية مع الناس الا و قد اكون شعرت بالف شعور .ما الحل   
66                                                                                                                                                                                       افكر كثير لدرجه تنسيني مافعلت او ماذا سوف افعل كثرة القلق والارق المزمن والشعور بالسلبيه والخوف قد يصل الم جسدي   

                                    answer         final_QT    final_AS  
146               تحتاج إلى علاج نفسي مكثف       ['A', 'B']       ['2']  
222                  العلاج النفسي هو الحل  ['A', 'C', 'E']       ['1']  
66   تمارين الاسترخاء و موسيقا ألفا مبدئيا       ['D', 'E']  ['1', '2']

### Start Cleaning Dataset
##  Data Preprocessing and Cleaning Overview

Before performing any analysis or model evaluation, it is crucial to clean and normalize the dataset to ensure consistency and quality.

This section outlines the preprocessing steps applied to the MentalQA Arabic dataset.

---

###  Cleaning Steps Applied:

1. **Displayed full text columns** – Enabled full visibility of long question/answer text using `pd.set_option("display.max_colwidth", None)`.
2. **Email Removal** – Removed any embedded email addresses using regular expressions.
3. **Separation Rules** – Inserted spaces between:
   - Arabic letters and numbers (e.g., "دواء20" → "دواء 20")
   - Arabic and English terms (e.g., "علاجmg" → "علاج mg")
   - Numbers and English words (e.g., "mg75" → "mg 75")
4. **Punctuation Cleanup** – Removed all punctuation marks except the Arabic question mark "؟".
5. **Arabic Letter Normalization** – Standardized variations of alef (ا), ta marbuta (ه), and others.
6. **Numeric Normalization** – Converted Arabic-Indic numerals (٠١٢...) to Western digits (012...).
7. **Repetition Reduction** – Compressed elongated words (e.g., "رااااائع" → "رائع").
8. **Question Mark Spacing** – Ensured space before and after "؟" to avoid it sticking to adjacent words.
9. **Custom Corrections** – Applied multiple custom dictionaries to fix common spelling errors, typos, and fused terms (e.g., "ماا" → "ما", "بلنتحار" → "بالانتحار").

---

###  Word-Level Error Detection via Frequency Analysis

To further enhance text quality, we analyzed both the cleaned questions and answers at the word level:

- Combined all tokens from `question_clean_1` and `answer_clean_1`.
- Used `collections.Counter` to calculate word frequencies.
- Created a sorted DataFrame to highlight rare and suspicious words.
- Manually reviewed low-frequency words to detect:
  - Typos (e.g., "هاذا", "معايا", "مفارقهمتصل")
  - Word merges and informal language
- Built custom correction dictionaries based on the findings to normalize the vocabulary.

This iterative refinement helped reduce vocabulary noise and improve input quality for downstream modeling.


In [ ]:
data.columns

Index(['question', 'answer', 'final_QT', 'final_AS'], dtype='object')

In [ ]:
data.shape

(350, 4)

In [ ]:
df = data[['question', 'answer']]
df

question  \
0                                                                                                                                                                                                                                                                                                هل يعتبر الخوف من عدم الإنجاب مستقبلاً حالة عادية خاصةً لما أكون متعلقة بأطفال كثيراً وأنا على وجه جواز أنا خايفة جداً   
1                                                                                                                                                                                                                                                              من سنه تقريبا و انا أذي نفسي ب اكثر من طريقة و ما اعرف كيف اتخلص من ذي العادة، و بدت تجيني افكار بإنهاء حياتي و حاولت انتحر باكثر من مرة و أكثر من طريقة   
2                                                                                                              السلام عليكم مشكلتي تقتصر على تكرار كلمة معينة لمدة طويلة من الزمن مثلا اذا سمعت شخص قام بتكرار كلمة معينة ابقى اكررها مع نفسي احاول توقيف نفسي ولكن دون جدوى حتى اصاب بلاحباط اصبت بهذا الشي من قبل والحمد لله تخلصت منه ولكنه رجع مع العلم ان الوسواس شائع في عائلتنا قالت امي استغفري بدل تكرار وشكرا   
3                                                                                                                                                                                                                                                                                                                                                              اكتئاب وفوبيا من المجتمع وانعزال وانطوائية وتعامل بسلبية   
4                                                                                                                                                                                                                                                                                       هل الإحساس بقرب الاجل و الخوف من الموت و الاحلام من اعراض الاكتئاب و القلق؟! و كيف يمكنني تخطي هذه المرحلة لان حياتي اصبحت جحيم   
5                                                                                                                                                                                                                                                            اهلا يا طبيب ، انا اعاني من عدة أعراض لمدة اسبوعين تقريبا . اعاني من حزن و ضيق في تنفس و بأفكار موت وايذاء نفسي وعدم رغبة بحياة . و اشعر بإرهاق بعض احيانا   
6                                                                                                                        انا مصاب باضطراب الشخصية الحديه ومريت بالعلاج الجدلي السلوكي ومتابع بالادويه لكنه مرض عقلي مزمن موروث لا يمكن علاجه، لذا سؤالي هل يتم البحث في مجال الصحه العقلية والاهتمام به أم لا ؟ وارجو ان اعرف مصدر لاتابع فيه اخر الابحاث لان بحثت في كل مكان تقريباً ولا اجد ما يبشرني ابداً .. وشكراً   
7                                                                                                          عاني من مشكلة الخوف من اذية الغرباء وعدم اخذ حقي منهم لذلك عندما اسير في الاماكن العامة يكون سيري بطريقة حذره وملفته للانتباه ربما ويقطه ولا استطيع التركيز واعاني صعوبة تذكر الكلمات الذي اردت قولها وايضاً اتذكر احداث الماضي واعاتب نفسي عليها مثل تأنيب الضمير واخاف من وقوع مكروه لي لدرجة كتمان ذلك ال   
8                                                                                                                                                                                                                                                                                                                                                  ماهو افضل دواء لعلاج المخاوف والقلق و الاكتئاب و تكون اعراضه بسيطة ؟   
9                                                                                                                                                                                                                                                                                                

In [ ]:
import re

def clean_arabic_text(text):
    if pd.isnull(text):
        return ""
    # 0. Normalize numbers
    text = text.translate(str.maketrans("٠١٢٣٤٥٦٧٨٩", "0123456789"))

    # 1. Remove Email (واستبداله بمسافة)
    text = re.sub(r'\S*@\S+', ' ', text)

    # 2. Make Distance between Arabic and Numbers/English
    text = re.sub(r'([ء-ي])(\d+)', r'\1 \2', text)
    text = re.sub(r'(\d+)([ء-ي])', r'\1 \2', text)
    text = re.sub(r'([ء-ي])([a-zA-Z]+)', r'\1 \2', text)
    text = re.sub(r'([a-zA-Z]+)([ء-ي])', r'\1 \2', text)
    text = re.sub(r'([a-zA-Z]+)(\d+)', r'\1 \2', text)
    text = re.sub(r'(\d+)([a-zA-Z]+)', r'\1 \2', text)

    # 3. Remove repeated characters (مثلاً: كييييف → كيف)
    text = re.sub(r'(.)\1{2,}', r'\1', text)

    # 4. Normalize Arabic letters
    text = re.sub(r'[إأآا]', 'ا', text)
    text = re.sub(r'ة', 'ه', text)
    text = re.sub(r'گ', 'ك', text)

    # 5. Remove punctuation (except ؟) مع استبدالها بمسافة
    text = re.sub(r'[^\w\s؟]', ' ', text)

    # 6. Ensure space before and after question mark
    text = re.sub(r'\s*؟\s*', ' ؟ ', text)

    # 7. Remove extra whitespaces
    text = re.sub(r'\s+', ' ', text).strip()

    return text

df["question_clean_1"] = df["question"].apply(clean_arabic_text)
df["answer_clean_1"] = df["answer"].apply(clean_arabic_text)

/tmp/ipython-input-3362103919.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["question_clean_1"] = df["question"].apply(clean_arabic_text)


In [ ]:
all_text = ' '.join(df['question_clean_1'].astype(str))
words = all_text.split()
word_freq = Counter(words)
freq_df = pd.DataFrame(word_freq.items(), columns=['word', 'count']).sort_values(by='count', ascending=True)
freq_df

word  count
1994          والنفور      1
1976              زنا      1
1974           بيومين      1
1973            زواجي      1
1972             موعد      1
1971           التونه      1
1970            البيض      1
1969            كريهه      1
1968            رائحه      1
1998            امضيت      1
1997          المرتبه      1
1977          الخطوبه      1
1993             مادا      1
1992           الصدمه      1
1990            للسبب      1
1989            خطبتي      1
1988             اراد      1
1986            للعلم      1
1985            تقبله      1
2015           للرسوب      1
2014            ابالي      1
2012              ضاع      1
3175          عالعلاج      1
1956            امارس      1
1955             السن      1
1954           الدرسه      1
1953             يؤثر      1
3182             امثل      1
3181            مصاعب      1
3180            شعوري      1
3179             عذاب      1
3178           تحاليل      1
3177             الين      1
2011             اعيد      1
3174           السؤال      1
3173          ولبترين      1
3171              200      1
3169           سوليان      1
3168            ومزاج      1
1983            يقترب      1
1982            اجعله      1
1980             قطعت      1
1979           تدهورت      1
1978            متعبه      1
2053            بفحصي      1
2036          بمضايقه      1
2035            وفجاه      1
2034             ادخن      1
2033            بدرجه      1
2063            بفتره      1
2062         المستشفى      1
2061            للضغط      1
2059            وبدات      1
2057            توجهت      1
2055           ارتفاع      1
2037           العروق      1
2051             وتعب      1
2050           الدوخه      1
2049             بنفس      1
2048           التالي      1
2078            ويظهر      1
2077            يزداد      1
2076             عصبي      1
2075          بالتكسي      1
2074           الركوب      1
2073           المسجد      1
2024           استطعت      1
2009            اتهرب      1
2008             اطيق      1
2006          التاليه      1
2005          للمرحله      1
2004             ادرس      1
2003           يسافرن      1
2002          زميلاتي      1
2001            العطل      1
2028            ماشيه      1
2026            تعاطي      1
1957          الرياضه      1
2022           بكميات      1
2020            بانجو      1
2047           وتحسنت      1
2045              مضى      1
2044              عدت      1
2043            مخدره      1
2042           وكانها      1
2040            اصابع      1
2039           بنهايه      1
1898             تجده      1
1879           تعقيدا      1
1878            تعطلت      1
1876           الاونه      1
1875             مرضى      1
1873         والمعارف      1
1872         الصداقات      1
1903              تعد      1
1902           يمكنها      1
1900            مسالم      1
1899             حنون      1
1882              تظن      1
1897            لكنها      1
1896            ضايقه      1
1895             عنيف      1
1894           سينتحر      1
1893           افترقا      1
1892            انهما      1
1891           اخبرها      1
1890           فراقها      1
1889             يخشى      1
1888           بالعجز      1
1866          المستفى      1
1851             ليست      1
1847          وضغوطات      1
1846           اختناق      1
1845           التوهم      1
1844           يعيشها      1
1842           وتحوله      1
1840            عمليه      1
1871            تكوين      1
1869          الطفوله      1
1867             خوفي      1
1919           وتعاني      1
1865             خارج      1
1862           مابعرف      1
1861             رجيم      1
1859       والكلسترول      1
1858              كلو      1
1856             ايكو      1
1887            لشعور      1
1886             يميل      1
1885              فهو      1
1884            لحديه      1
1937             اوقف      1
1921              ساء      1
1920           جرثومه      1
1951           وتعديل      1
1948         المذاكره      1
1947              يضر      1
1945           

In [ ]:
def apply_custom_corrections(text):
    corrections = {
        "قي": "في",
        "انااذكر": "أنا أذكر",
        "ماا": "ما",
        "عليكماعاني": "عليكم اعاني",
        "هده": "هذه",
        "للاكتئا": "للاكتئاب",
        "بلسوء": "ب السوء",
        "ءاذي": "الذي",
        "ماكدر": "ما اقدر",
        "معايا": "معي",
        "حتا": "حتى",
        "انوا": "أنه",
        "اخري": "أخرى",
        "بلنتحار": "ب الانتحار",
        "بلاحباط": "ب الإحباط",
        "منهاا": "منها",
        "ابغا": "أريد",
        "طمانتني": "طمنتني",
        "وواحبها": "واحبها",
        "مفعولخ": "مفعوله",

    }

    for wrong, right in corrections.items():
        text = text.replace(wrong, right)
    return text

df["question_clean_2"] = df["question_clean_1"].apply(apply_custom_corrections)
#df["answer_clean_2"] = df["answer_clean_1"].apply(clean_arabic_text)

In [ ]:
all_text_ = ' '.join(df['answer_clean_1'].astype(str))
words_ = all_text_.split()
word_freq_ = Counter(words_)
freq_df_ = pd.DataFrame(word_freq_.items(), columns=['word', 'count']).sort_values(by='count', ascending=True)
freq_df_

word  count
3825                   تعالج      1
3826                  بنتائج      1
17                     يتحقق      1
18                       هدا      1
21                      مضار      1
24                    ودعينى      1
25                      اشير      1
29                    نتعامل      1
2558                   صادقا      1
2528                    الحب      1
2529                 وانهيار      1
2530                الدفاعات      1
2531                      ضد      1
2532                   دفعات      1
2533                 العدوان      1
2534                  الجنسي      1
3805                    يفهم      1
3823                 المبكره      1
3809                   لاحظت      1
3810                   هالشي      1
3811                  تجاوزه      1
3812                     تصف      1
3813                       ح      1
3814                     كتب      1
3815                الانترنت      1
3817                   تدفعك      1
3818                   لتوهم      1
3819                   انشغل      1
3820                 اوالعمل      1
3821                    تلقي      1
3808                    اسرغ      1
3822                  والصبر      1
53                    هنداوى      1
54                    مستشار      1
55                    والعقم      1
56                    والغدد      1
57                     وطفال      1
58                  الانابيب      1
59                     مدينه      1
60                    الحسين      1
62                    الاردن      1
32                     اخصائ      1
35                   الاحباط      1
36                      التى      1
37                       تتم      1
39                    بمرحله      1
40                    النفاس      1
42                       رفض      1
3782                   تندرج      1
3783                    مسمى      1
3784                   ويشمل      1
3785                  ونوبات      1
3786                  لتمييز      1
3787                 التسخيص      1
3788                  مراجغه      1
3789                  مناسبه      1
67                   اختصاصي      1
71                  بالتشخيص      1
74                  بالجلسات      1
75                  والادويه      1
49                      نتعا      1
50                        مل      1
51                      معهز      1
52                  دابراهيم      1
3773                    بقله      1
80                   الشاءعه      1
85                   وسواسيه      1
88                     افعال      1
89                     ويلعب      1
90                      عامل      1
91                   الوراثه      1
92                       دور      1
3806                العقلانى      1
3807                 المعرفى      1
3776                    واجب      1
3777                 الوسوسه      1
3778                    ضاره      1
3779                  بالعقل      1
3780                  والجسم      1
3781                   تدربي      1
106                    نتائج      1
3790                بالتاكيد      1
3791          والاسترخاءوهذا      1
3760                للانفعال      1
3761                   لدرجه      1
3762                   فنيات      1
3763                  واداره      1
3764                 ومهارات      1
3765                والمشاكل      1
3766                هوالعلاج      1
3767                  خلافات      1
3768                  لزياره      1
3769                     ادق      1
3770                 ولمعرفه      1
3771                  علامات      1
3772                    بدات      1
3749               الاخرفتصل      1
3750                المعلومه      1
3751                  احدهما      1
3752             الاخروعندما      1
3753                   الاخر      1
3754                     مرت      1
3755                      بي      1
3756                  وتختفي      1
3757                والعصبيه      1
142                   العلمى      1
114                   تستجيب      1
116                     وحده      1
117                   للكثير      1
126                    سيوصف      1
97                     دواءي

In [ ]:
def apply_answer_corrections(text):
    corrections = {
        "النفسيوربما": "النفسي وربما",
        "العقاقيرويستحسن": "العقاقير ويستحسن",
        "وضروريوايذاء": "و ضروري و إيذاء",
        "والجرعهليقدرها": "و الجرعة ليقدرها",
        "تسوءوربما": "تسوء وربما",
        "تغييراو": "تغيير أو",
        "ابق": "أبقى",
        "الادويهنحتاج": "الأدوية نحتاج",
        "الاعتماديهالاعتماد": "الاعتمادية الاعتماد",
        "الحلتدريجيا": "الحل تدريجا",
        "مفارقهالتعلق": "مفارقة التعلق",
        "خطيرهلانها": "خطيرة لأنها",
        "نفسيالافكاراالانتحاريه": "نفسي الأفكار الانتحارية",
        "الخضارقللي": "الخضار قللي",
        "غلى": "على",
        "الجتماعي": "الاجتماعي",
        "لكليهماونتوقف": "لكليهما و نتوقف",
        "وانواعهاولوم": "و أنواعها و لوم",
        "الناسنحتاج": "الناس نحتاج",
        "المراءه": "المراة",
        "هاذا": "هذا",
        "المسسبه": "المسببه",
        "اى": "اي",
        "عضوى": "عضوي",
        "النفسانيالافكار": "النفساني الأفكار",
        "هدا": "هذا",
        "اسرغ": "اسرع",
        "والاسترخاءوهذا": "و الاسترخاء و هذا",
        "الاخرفتصل": "الاخر فتصل",
        "الاخروعندما": "الاخر و عندما",
        "دواءي": "دوائي",
        "مشهورهاسمها": "مشهور اسمه"
    }

    for wrong, right in corrections.items():
        text = text.replace(wrong, right)
    return text

df["answer_clean_2"] = df["answer_clean_1"].apply(apply_answer_corrections)

In [ ]:
# Cleaning Columns
df[['question_clean_2', 'answer_clean_2']]

question_clean_2  \
0                                                                                                                                                                                                                                                                                                    هل يعتبر الخوف من عدم الانجاب مستقبلا حاله عاديه خاصه لما اكون متعلقه باطفال كثيرا وانا على وجه جواز انا خايفه جدا   
1                                                                                                                                                                                                                                                               من سنه تقريبا و انا اذي نفسي ب اكثر من طريقه و ما اعرف كيف اتخلص من ذي العاده و بدت تجيني افكار بانهاء حياتي و حاولت انتحر باكثر من مره و اكثر من طريقه   
2                                                                                                            السلام عليكم مشكلتي تقتصر على تكرار كلمه معينه لمده طويله من الزمن مثلا اذا سمعت شخص قام بتكرار كلمه معينه ابقى اكررها مع نفسي احاول توفيف نفسي ولكن دون جدوى حتى اصاب ب الإحباط اصبت بهذا الشي من قبل والحمد لله تخلصت منه ولكنه رجع مع العلم ان الوسواس شائع في عائلتنا قالت امي استغفري بدل تكرار وشكرا   
3                                                                                                                                                                                                                                                                                                                                                              اكتئاب وفوبيا من المجتمع وانعزال وانطوائيه وتعامل بسلبيه   
4                                                                                                                                                                                                                                                                                       هل الاحساس بقرب الاجل و الخوف من الموت و الاحلام من اعراض الاكتئاب و القلق ؟ و كيف يمكنني تخطي هذه المرحله لان حياتي اصبحت جحيم   
5                                                                                                                                                                                                                                                                  اهلا يا طبيب انا اعاني من عده اعراض لمده اسبوعين تقريبا اعاني من حزن و ضيق في تنفس و بافكار موت وايذاء نفسي وعدم رغبه بحياه و اشعر بارهاق بعض احيانا   
6                                                                                                                               انا مصاب باضطراب الشخصيه الحديه ومريت بالعلاج الجدلي السلوكي ومتابع بالادويه لكنه مرض عقلي مزمن موروث لا يمكن علاجه لذا سؤالي هل يتم البحث في مجال الصحه العقليه والاهتمام به ام لا ؟ وارجو ان اعرف مصدر لاتابع فيه اخر الابحاث لان بحثت في كل مكان تقريبا ولا اجد ما يبشرني ابدا وشكرا   
7                                                                                                           عاني من مشكله الخوف من اذيه الغرباء وعدم اخذ حفي منهم لذلك عندما اسير في الاماكن العامه يكون سيري بطريقه حذره وملفته للانتباه ربما ويقطه ولا استطيع التركيز واعاني صعوبه تذكر الكلمات الذي اردت قولها وايضا اتذكر احداث الماضي واعاتب نفسي عليها مثل تانيب الضمير واخاف من وقوع مكروه لي لدرجه كتمان ذلك ال   
8                                                                                                                                                                                                                                                                                                                                                  ماهو افضل دواء لعلاج المخاوف والقلق و الاكتئاب و تكون اعراضه بسيطه ؟   
9                                                                                                                                                                                                                                                                                        

In [ ]:
GROQ_API_KEY="gsk_...."
from langchain_groq import ChatGroq
from langchain.schema import HumanMessage


chat = ChatGroq(
    groq_api_key=GROQ_API_KEY,
    model_name="llama3-70b-8192",
    temperature=0.1,
    max_tokens=1024
)

In [ ]:
def build_zero_shot_prompt(question):
    return f"أجب على السؤال التالي باحترافية وباللغة العربية:\n\nالسؤال: {question}\n\nالإجابة:"

In [ ]:
def generate_llama_answer(question):
    prompt = build_zero_shot_prompt(question)
    response = chat.invoke([
        HumanMessage(content=prompt)
    ])
    return response.content.strip()


In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_zero_shot_answer'] = sample_df['question_clean_2'].apply(generate_llama_answer)
sample_df.to_csv("llama3_zero_shot_generated_answers.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_zero_shot_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_f1'] = F1.tolist()
sample_df.to_csv("llama3_zero_shot_generated_answers.csv", index=False)
print(f"✅ Average BERTScore F1: {F1.mean().item():.2f}")

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 28.35 seconds, 0.35 sentences/sec
✅ Average BERTScore F1: 0.61


In [ ]:
example_1 = {
    "question": "بقالي اكتر من اسبوعين مش بنام ولا باكل و لو نمت ساعه واحده في اليوم افضل صاحيه 3 ايام و بحلم بكابوس بيتكرر علي طول اني باذى نفسي لدرجه اني فكرت في كده	",
    "answer": "أنتي بحاجه لزيارة طبيب نفسي للتقيم اخذ السيره المرضيه بشكل ادق ولمعرفة تفاصيل اخرى مهمه في التشخيص لا تترددي في الاستشاره لان علامات المرض النفسي الحاد بدات تظهر بقله الحاجه للنوم تمنياتي بالشفاء العاجل	"
}

example_2 = {
    "question": "تمنعني ظروف ما اقدر اروح دكتور اخصائي ولا اشرح حالتي كدامه صرت افكر بالانتحار بسبب هاي الحاله شي مخيف أشد أنواع العذاب لدرجه الموت أهون الموت أهون	",
    "answer": "السلام عليكم علاج الادمان محتاج طبيب وادوية والاهم يكون عندك اراده قويه للتخلص من هذه السموم وعلى قدر عزيمتك هيكون التوفيق لنجاح العلاج ساعد نفسك	"
}

example_3 = {
    "question": "اعاني من الخوف وتنبؤات من كلام اهلي وبصمتهم انهم يبون يقتلوني بدون سبب والي محرضهم ابوي",
    "answer": "التقلبات المزاجيه في سنك المبكره كثيره ومن المفيد مراجعه طبيب للتشخيص الدقيق	"
}


In [ ]:
def build_fewshot_prompt(new_question):
    prompt = f"""
أجب على الأسئلة التالية باحترافية وباللغة العربية:

س: {example_1['question']}
ج: {example_1['answer']}

س: {example_2['question']}
ج: {example_2['answer']}

س: {example_3['question']}
ج: {example_3['answer']}

س: {new_question}
ج:"""
    return prompt.strip()

In [ ]:
def generate_llama_answer(question):
    prompt = build_fewshot_prompt(question)
    response = chat.invoke([
        HumanMessage(content=prompt)
    ])
    return response.content.strip()


In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_few_shot_answer'] = sample_df['question_clean_2'].apply(generate_llama_answer)
sample_df.to_csv("llama_few_shot_answer.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_few_shot_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_f1'] = F1.tolist()
sample_df.to_csv("llama_few_shot_answer.csv", index=False)
print(f"✅ Average BERTScore F1: {F1.mean().item():.2f}")

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 8.81 seconds, 1.13 sentences/sec
✅ Average BERTScore F1: 0.66


In [ ]:
import random

def generate_fewshot_sc_answer(question, n=10): # I traied 5 answers then 10 anwsers but the F1 is same
    answers = []
    for _ in range(n):
        prompt = build_fewshot_prompt(question)
        response = chat.invoke(prompt, temperature=0.1)
        answer = response.content.strip()
        answers.append(answer)

    most_common = Counter(answers).most_common(1)[0][0]
    return most_common

In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_fewshot_sc_answer'] = sample_df['question_clean_2'].apply(generate_fewshot_sc_answer)
sample_df.to_csv("llama_fewshot_sc_answer.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_fewshot_sc_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_f1'] = F1.tolist()
sample_df.to_csv("llama_fewshot_sc_answer.csv", index=False)
print(f"✅ Average BERTScore F1: {F1.mean().item():.2f}")

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 9.10 seconds, 1.10 sentences/sec
✅ Average BERTScore F1: 0.66


In [ ]:
def generate_multiple_llama_answers(question, n=5):
    answers = []
    for _ in range(n):
        prompt = build_fewshot_prompt(question)
        response = chat.invoke(prompt, temperature=0.1)
        answers.append(response.content.strip())
    return answers

In [ ]:
def build_refinement_prompt(question, answers):
    joined_answers = "\n\n".join(
    [f"Answer {i+1}: {ans}" for i, ans in enumerate(answers)]
    )

    return f"""Question: {question}

    These are different answers to the same question:

    {joined_answers}

    Based on the previous answers, write an improved and ideal answer, taking into account accuracy and clarity:

Final answer:"""

In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_er_answer'] = sample_df['question_clean_2'].apply(
    lambda q: build_refinement_prompt(q, generate_multiple_llama_answers(q, n=5))
)
sample_df.to_csv("llama_er_answer.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_er_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_er_answer'] = F1.tolist()
sample_df.to_csv("llama_er_answer.csv", index=False)
print(f"✅ Average BERTScore F1: {F1.mean().item():.2f}")

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 24.64 seconds, 0.41 sentences/sec
✅ Average BERTScore F1: 0.61


In [ ]:
example_1 = {
    "question": "بقالي اكتر من اسبوعين مش بنام ولا باكل و لو نمت ساعه واحده في اليوم افضل صاحيه 3 ايام و بحلم بكابوس بيتكرر علي طول اني باذى نفسي لدرجه اني فكرت في كده	",
    "answer": "أنتي بحاجه لزيارة طبيب نفسي للتقيم اخذ السيره المرضيه بشكل ادق ولمعرفة تفاصيل اخرى مهمه في التشخيص لا تترددي في الاستشاره لان علامات المرض النفسي الحاد بدات تظهر بقله الحاجه للنوم تمنياتي بالشفاء العاجل	"
}

example_2 = {
    "question": "تمنعني ظروف ما اقدر اروح دكتور اخصائي ولا اشرح حالتي كدامه صرت افكر بالانتحار بسبب هاي الحاله شي مخيف أشد أنواع العذاب لدرجه الموت أهون الموت أهون	",
    "answer": "السلام عليكم علاج الادمان محتاج طبيب وادوية والاهم يكون عندك اراده قويه للتخلص من هذه السموم وعلى قدر عزيمتك هيكون التوفيق لنجاح العلاج ساعد نفسك	"
}

example_3 = {
    "question": "اعاني من الخوف وتنبؤات من كلام اهلي وبصمتهم انهم يبون يقتلوني بدون سبب والي محرضهم ابوي",
    "answer": "التقلبات المزاجيه في سنك المبكره كثيره ومن المفيد مراجعه طبيب للتشخيص الدقيق	"
}

example_4 = {
    "question": "عمرها 15 منذ قرابه شهرين او اكثر بدات حالتها تتغير من الهدوء الى العصبيه وعدم النوم",
    "answer": "هناك العديد من الاسئله هل يوجد خلافات في المنزل هل تعرضت لاي ضغوط او اي صدمه ؟ يمكنك التواصل مباشره مع معالج نفسي للمساعده"
}

example_5 = {
    "question": "قلق وتوتر ووسواس قهري وتاتاه في الكلام وعجز داخلي اظن اني مكروه واني لا اقدر افعل شي	",
    "answer": "انشغل بالدراسه اوالعمل او الانشطه الاجتماعيه ومع تلقي العلاج النفسي تتحسن الحاله مع التدريب والصبر"
}


In [ ]:
def build_fewshot_5_prompt(new_question):
    prompt = f"""
أجب على الأسئلة التالية باحترافية وباللغة العربية:

س: {example_1['question']}
ج: {example_1['answer']}

س: {example_2['question']}
ج: {example_2['answer']}

س: {example_3['question']}
ج: {example_3['answer']}

س: {example_4['question']}
ج: {example_4['answer']}

س: {example_5['question']}
ج: {example_5['answer']}

س: {new_question}
ج:"""
    return prompt.strip()

In [ ]:
def generate_llama_fewshot_5_answer(question):
    prompt = build_fewshot_5_prompt(question)
    response = chat.invoke([
        HumanMessage(content=prompt)
    ])
    return response.content.strip()

In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_fewshot_5_answer'] = sample_df['question_clean_2'].apply(generate_llama_fewshot_5_answer)
sample_df.to_csv("llama_fewshot_5_answer.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_fewshot_5_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_fewshot_5'] = F1.tolist()
sample_df.to_csv("llama_fewshot_5_answer.csv", index=False)
print(f"✅ 5 - Few-Shot BERTScore F1: {F1.mean().item():.2f}")

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 11.81 seconds, 0.42 sentences/sec
✅ 5 - Few-Shot BERTScore F1: 0.62


In [ ]:
def build_fewshot_cot_prompt(new_question):
    prompt = f"""

Question: I can't sleep and feel stressed all day. Do I have a mental illness?

Let's analyze the condition gradually:
1. Look at the symptoms: insomnia (inability to sleep) and constant stress.
2. Associated with: disorders such as generalized anxiety or depression.
3. To properly diagnose the condition: You must know a few things.
4. To answer: Provide a professional answer that takes into account the above factors using one or more of the strategies:
- providing information
- Direct answers
- Emotional support

Answer: It is best to consult a psychologist to evaluate the condition. Lifestyle changes or behavioral therapy may help alleviate the symptoms.

Make sure your answer is fully formatted in Arabic and specifically designed to diagnose mental health conditions

Question: {new_question}
Answer:"""
    return prompt.strip()

In [ ]:
def generate_llama_fewshot_cot_answer(question):
    prompt = build_fewshot_cot_prompt(question)
    response = chat.invoke([
        HumanMessage(content=prompt)
    ])
    return response.content.strip()

In [ ]:
sample_df = df[['question_clean_2', 'answer_clean_2']].sample(n=10, random_state=42).copy()
sample_df['llama_fewshot_cot_answer'] = sample_df['question_clean_2'].apply(generate_llama_fewshot_cot_answer)
sample_df.to_csv("llama_fewshot_cot_answer.csv", index=False)

In [ ]:
from bert_score import score

P, R, F1 = score(
    sample_df['llama_fewshot_cot_answer'].tolist(),
    sample_df['answer_clean_2'].tolist(),
    lang="ar",
    verbose=True
)

sample_df['bertscore_llama_fewshot_cot_answer'] = F1.tolist()
sample_df.to_csv("llama_fewshot_cot_answer.csv", index=False)
print(f"✅ CoT BERTScore F1: {F1.mean().item():.2f}")

calculating scores...
computing bert embedding.


  0%|          | 0/1 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/torch/nn/modules/module.py:1750: FutureWarning: `encoder_attention_mask` is deprecated and will be removed in version 4.55.0 for `BertSdpaSelfAttention.forward`.
  return forward_call(*args, **kwargs)


computing greedy matching.


  0%|          | 0/1 [00:00<?, ?it/s]

done in 24.67 seconds, 0.41 sentences/sec
✅ CoT BERTScore F1: 0.62


In [6]:
!pip install -U google-generativeai

In [2]:
from huggingface_hub import login
login()  # أدخل توكن HF

In [8]:
import google.generativeai as genai
print(f"Google Generative AI version: {genai.__version__}")

Google Generative AI version: 0.8.5


In [3]:
from huggingface_hub import __version__ as hf_version
print(f"Hugging Face Hub version: {hf_version}")

Hugging Face Hub version: 0.34.3


In [5]:
import sys
print(f"Python version: {sys.version}")

Python version: 3.11.13 (main, Jun  4 2025, 08:57:29) [GCC 11.4.0]


In [ ]:
from transformers import AutoModelForCausalLM, AutoTokenizer

# Allam
allam_model = AutoModelForCausalLM.from_pretrained("ALLaM-AI/ALLaM-7B-Instruct-preview", torch_dtype="auto", device_map="auto")
allam_tokenizer = AutoTokenizer.from_pretrained("ALLaM-AI/ALLaM-7B-Instruct-preview")

# Qwen
qwen_model = AutoModelForCausalLM.from_pretrained("Qwen/Qwen2.5-7B-Instruct", torch_dtype="auto", device_map="auto")
qwen_tokenizer = AutoTokenizer.from_pretrained("Qwen/Qwen2.5-7B-Instruct")

config.json:   0%|          | 0.00/686 [00:00<?, ?B/s]

model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/4.03G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/243 [00:00<?, ?B/s]

tokenizer_config.json: 0.00B [00:00, ?B/s]

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

In [ ]:
# FINAL aLLAm
def gen_hf(model, tokenizer, prompt):
    # 1. Tokenize the prompt and move to model's device
    toks = tokenizer(prompt, return_tensors="pt").to(model.device)

    # 2. Generate the model output
    out = model.generate(**toks, max_new_tokens=1024, temperature=0.1, do_sample=True, top_p=0.9)

    # 3. Decode only the generated part (exclude input prompt)
    generated_tokens = out[0][toks["input_ids"].shape[1]:]
    response = tokenizer.decode(generated_tokens, skip_special_tokens=True)

    return response


In [ ]:
# FINAL Qwen
def gen_qwen(model, tokenizer, prompt):
    # 1. Tokenize the prompt and move to model's device
    toks = tokenizer(prompt, return_tensors="pt").to(model.device)

    # 2. Generate output
    out = model.generate(**toks, max_new_tokens=1024, temperature=0.1, do_sample=True, top_p=0.9)

    # 3. Decode only the generated part
    generated_tokens = out[0][toks["input_ids"].shape[1]:]
    response = tokenizer.decode(generated_tokens, skip_special_tokens=True)

    return response

In [ ]:
# FINAL Gemini
import google.generativeai as genai
genai.configure(api_key="..")
gemini_model = genai.GenerativeModel("gemini-2.5-flash")

def gen_gemini(model, prompt, max_output_tokens=1024, temperature=0.1, top_p=0.9):
    response = model.generate_content(prompt)
    return response.text


In [ ]:
#FINAL GPT

import openai

openai.api_key = "sk-proj...."
openai_model = "gpt-4o"

def gen_openai(prompt, model_name):
    response = openai.ChatCompletion.create(
        model=model_name,
        messages=[
            {"role": "user", "content": prompt}], max_tokens=1024,
                            temperature=0.1,
                            top_p=0.9
                            )
    return response.choices[0].message.content

In [ ]:
# FINAL

import pandas as pd
from tqdm import tqdm
from bert_score import score

# Load 15 samples
#df = pd.read_csv("Train_Dev.tsv", sep="\t")
df_sample = df[['question_clean_2', 'answer_clean_2']].dropna().sample(n=20, random_state=42).reset_index(drop=True)

# Prepare all prompts
df_sample["prompt"] = df_sample["question_clean_2"].apply(build_fewshot_prompt)

# Initialize result containers
results = {
    "allam": [],
    "qwen": [],
    "gpt": [],
    "gemini": []
}


In [ ]:
#FINAL

# Allam
for prompt in tqdm(df_sample["prompt"], desc="Allam"):
    ans = gen_hf(allam_model, allam_tokenizer, prompt)
    results["allam"].append(ans)

# Qwen
for prompt in tqdm(df_sample["prompt"], desc="Qwen"):
    ans = gen_qwen(qwen_model, qwen_tokenizer, prompt)
    results["qwen"].append(ans)

# OpenAI GPT
for prompt in tqdm(df_sample["prompt"], desc="GPT"):
    ans = gen_openai(prompt, openai_model)
    results["gpt"].append(ans)

# Gemini
for prompt in tqdm(df_sample["prompt"], desc="Gemini"):
    ans = gen_gemini(gemini_model, prompt)
    results["gemini"].append(ans)


Allam:   5%|▌         | 1/20 [1:17:59<24:41:51, 4679.53s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


In [ ]:
bert_results = {}

for model_name in results.keys():
    print(f"Scoring {model_name}...")
    P, R, F1 = score(
        results[model_name],
        df_sample["answer_clean_2"].tolist(),
        lang="ar",
        verbose=True
    )
    bert_results[model_name] = {
        "precision": P.mean().item(),
        "recall": R.mean().item(),
        "f1": F1.mean().item()
    }


In [ ]:
print("\n📊 Final Average BERTScore F1 per Model:")
for model_name, scores in bert_results.items():
    print(f"{model_name}: F1 = {scores['f1']:.4f}")